In [ ]:
# ✅ الخطوة 1: تثبيت YOLOv8
!pip install ultralytics --upgrade -q
from ultralytics import YOLO
import os, zipfile

# ✅ الخطوة 2: ربط Google Drive
from google.colab import drive
drive.mount('/content/drive')

# ✅ الخطوة 3: تحديد مسار ملف ZIP داخل Google Drive
zip_path = '/content/drive/MyDrive/Dataset.zip'
dataset_dir = 'Dataset'

# ✅ الخطوة 4: فك ضغط الملف
with zipfile.ZipFile(zip_path, 'r') as zip_ref:
    zip_ref.extractall(dataset_dir)

# ✅ الخطوة 5: التأكد من محتويات Dataset
print("محتويات مجلد Dataset:")
!find Dataset -type f

# ✅ الخطوة 6: تعديل مسار data.yaml بناءً على محتويات المجلد
# بعد رؤية النتائج، عدلي المسار هنا:
yaml_path = os.path.join(dataset_dir, 'Dataset/data.yaml')  # عدليه إذا كان داخل مجلد فرعي

with open(yaml_path, 'r') as f:
    yaml_data = f.read()

yaml_data = yaml_data.replace('C:/Users/HP/Desktop/Dataset/images/train', 'images/train')
yaml_data = yaml_data.replace('C:/Users/HP/Desktop/Dataset/images/val', 'images/val')

with open(yaml_path, 'w') as f:
    f.write(yaml_data)

# ✅ الخطوة 7: تدريب YOLOv8
model = YOLO('yolov8n.pt')

results = model.train(
    data=yaml_path,
    epochs=150,
    imgsz=640,
    project='EvAREST_Train',
    name='yolov8_text',
    exist_ok=True,
    freeze=22,
    hsv_h=0.015,
    hsv_s=0.7,
    hsv_v=0.4,
    degrees=5.0,
    translate=0.1,
    scale=0.5,
    shear=0.0,
    perspective=0.0,
    flipud=0.0,
    fliplr=0.5,
    mosaic=1.0,
    mixup=0.0,
    copy_paste=0.0,
    patience=50,
    val=True
)


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 34.2 MB/s eta 0:00:00
Creating new Ultralytics Settings v0.0.6 file ✅ 
View Ultralytics Settings with 'yolo settings' or at '/root/.config/Ultralytics/settings.json'
Update Settings with 'yolo settings key=value', i.e. 'yolo settings runs_dir=path/to/dir'. For help see https://docs.ultralytics.com/quickstart/#ultralytics-settings.
Mounted at /content/drive
محتويات مجلد Dataset:
Dataset/Dataset/labels/train/img_107.txt
Dataset/Dataset/labels/train/img_351.txt
Dataset/Dataset/labels/train/img_8.txt
Dataset/Dataset/labels/train/img_290.txt
Dataset/Dataset/labels/train/img_311.txt
Dataset/Dataset/labels/train/img_276.txt
Dataset/Dataset/labels/train/img_195.txt
Dataset/Dataset/labels/train/img_330.txt
Dataset/Dataset/labels/train/img_141.txt
Dataset/Dataset/labels/train/img_342.txt
Dataset/Dataset/labels/train/img_126.txt
Dataset/Dataset/labels/train/img_348.txt
Dataset/Dataset/labels/train/img_145.txt
Dataset/Dataset/labels/train/img_

In [ ]:
from google.colab import drive
import shutil

# 1. اربط Google Drive
drive.mount('/content/drive')

# 2. المسار الأصلي في Colab
source_dir = '/content/EvAREST_Train'

# 3. المسار المراد حفظ المجلد فيه في Google Drive
destination_dir = '/content/drive/MyDrive/EvAREST_Train_weights'

# 4. نسخ المجلد كامل
shutil.copytree(source_dir, destination_dir)

print(f"تم نسخ المجلد بنجاح إلى {destination_dir}")

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
تم نسخ المجلد بنجاح إلى /content/drive/MyDrive/EvAREST_Train_weights


In [ ]:
# ✅ 1) تثبيت YOLOv8
!pip install -q ultralytics --upgrade
from ultralytics import YOLO
import os, zipfile

# ✅ 2) ربط Google Drive
from google.colab import drive
drive.mount('/content/drive')

# ✅ 3) تحديد مسار ملف ZIP داخل Google Drive
zip_path = '/content/drive/MyDrive/Dataset.zip'
dataset_dir = 'Dataset'

# ✅ 4) فك ضغط الملف
if not os.path.exists(dataset_dir):
    with zipfile.ZipFile(zip_path, 'r') as z:
        z.extractall(dataset_dir)

# ✅ 5) التأكد من المحتويات
print("محتويات مجلد Dataset:")
!find Dataset -type f | head -n 40

# ✅ 6) تعديل مسار data.yaml (عدّل المسار حسب بنية مجلدك بعد الفك)
yaml_path = os.path.join(dataset_dir, 'Dataset/data.yaml')  # غيّره لو كان بمكان مختلف
with open(yaml_path, 'r') as f:
    y = f.read()
y = y.replace('C:/Users/HP/Desktop/Dataset/images/train', 'images/train')
y = y.replace('C:/Users/HP/Desktop/Dataset/images/val', 'images/val')
with open(yaml_path, 'w') as f:
    f.write(y)

# ✅ 7) التحضير للنموذج (نفس وزن YOLOv8n pretrained)
base_weights = 'yolov8n.pt'
model = YOLO(base_weights)

project = 'EvAREST_Train'
run_name_stage1 = 'yolov8_text_ft_s1'
run_name_stage2 = 'yolov8_text_ft_s2'

# ============== المرحلة 1: نجمّد جزء من الظهر (Backbone) وندرب الرأس فقط ==============
# ملاحظات:
# - freeze=10: يجمّد أوّل N طبقات (القيمة 10 غالبًا تغطي معظم العمود الفقري بدون الرأس)
# - cos_lr: جدولة كوزاين تساعد على استقرار التعلم
# - close_mosaic=10: يوقف Mosaic في آخر 10 إيبكس لثبات التدريب
stage1 = model.train(
    data=yaml_path,
    epochs=30,
    imgsz=640,
    batch=-1,                 # حجم دفعة تلقائي (حوالي 60% من ذاكرة GPU)
    project=project,
    name=run_name_stage1,
    exist_ok=True,
    seed=0,
    freeze=10,                # ❄️ درّب الرأس أولًا
    lr0=0.005,                # أخفض قليلًا كبداية للرأس
    lrf=0.1,
    cos_lr=True,
    close_mosaic=10,
    optimizer='AdamW',
    weight_decay=0.0005,
    hsv_h=0.015, hsv_s=0.7, hsv_v=0.4,
    degrees=5.0, translate=0.1, scale=0.5,
    shear=0.0, perspective=0.0,
    flipud=0.0, fliplr=0.5,
    mosaic=1.0, mixup=0.0, copy_paste=0.0,
    patience=50,
    val=True
)

# ============== المرحلة 2: نفك كل الطبقات ونكمّل Fine-tune بمعدل تعلّم أصغر ==============
# نحمّل أفضل وزن من المرحلة 1 ونبدأ تجربة جديدة (بدلاً من resume حتى تُطبّق إعدادات جديدة بالكامل)
best_s1 = f'{project}/{run_name_stage1}/weights/best.pt'
model2 = YOLO(best_s1)

stage2 = model2.train(
    data=yaml_path,
    epochs=120,               # زوّد كما تحتاج (إجمالي ≈ 150+)
    imgsz=640,                # جرّب 704 أو 768 إذا تسمح الذاكرة لزيادة mAP
    batch=-1,
    project=project,
    name=run_name_stage2,
    exist_ok=True,
    seed=0,
    freeze=0,                 # 🔓 فكّ كل الطبقات
    lr0=0.001,                # أصغر لأننا نحدّث كل الشبكة
    lrf=0.05,
    cos_lr=True,
    close_mosaic=10,
    optimizer='AdamW',
    weight_decay=0.0005,
    patience=50,
    val=True
)

print("✅ انتهت مرحلتا الـ fine-tuning. المسارات:")
print(f"Stage1: {project}/{run_name_stage1}")
print(f"Stage2: {project}/{run_name_stage2}")


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 21.7 MB/s eta 0:00:00
Creating new Ultralytics Settings v0.0.6 file ✅ 
View Ultralytics Settings with 'yolo settings' or at '/root/.config/Ultralytics/settings.json'
Update Settings with 'yolo settings key=value', i.e. 'yolo settings runs_dir=path/to/dir'. For help see https://docs.ultralytics.com/quickstart/#ultralytics-settings.
Mounted at /content/drive
محتويات مجلد Dataset:
Dataset/Dataset/images/train/img_148.jpg
Dataset/Dataset/images/train/img_363.jpg
Dataset/Dataset/images/train/img_196.jpg
Dataset/Dataset/images/train/img_145.jpg
Dataset/Dataset/images/train/img_332.jpg
Dataset/Dataset/images/train/img_247.jpg
Dataset/Dataset/images/train/img_303.jpg
Dataset/Dataset/images/train/img_361.jpg
Dataset/Dataset/images/train/img_34.jpg
Dataset/Dataset/images/train/img_346.jpg
Dataset/Dataset/images/train/img_299.jpg
Dataset/Dataset/images/train/img_258.jpg
Dataset/Dataset/images/train/img_270.jpg
Dataset/Dataset/images/train/img

In [ ]:
from google.colab import drive
import shutil

# 1. اربط Google Drive
drive.mount('/content/drive')

# 2. المسار الأصلي في Colab
source_dir = '/content/EvAREST_Train'

# 3. المسار المراد حفظ المجلد فيه في Google Drive
destination_dir = '/content/drive/MyDrive/EvAREST_Train_weights2'

# 4. نسخ المجلد كامل
shutil.copytree(source_dir, destination_dir)

print(f"تم نسخ المجلد بنجاح إلى {destination_dir}")

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
تم نسخ المجلد بنجاح إلى /content/drive/MyDrive/EvAREST_Train_weights2
